# Rheostat Attempt 5
## Bioscrape

In [3]:
#Using Bioscrape: Basic Imports

#A Model is a CRN with some bells and whistles
from bioscrape.types import Model

#py_simulate_model is a helper function that takes care of may details for you
from bioscrape.simulator import py_simulate_model

#For arrays and plotting
import numpy as np
import pylab as plt

# Import good plotting packages 
import bokeh.io
import bokeh.plotting
from bokeh.layouts import row
#import bokeh_catplot
import panel as pn
pn.extension()


bokeh.io.output_notebook()

Loading BokehJS ...

Let's first lay out the key take-aways from **meeting with William (5.1.2020)**
- Use cell biology by the numbers to get values for [enzyme], [atp], [glucose], believable $k_b$, $k_{uf}$, $k_{ur}$, and $k_{catalysis}$.
    - Figure out how much 3PGA is used in cell extract in Murray Lab (from tx/tl papers?)
    - make sure to consider units
- Get units of time to understand how fast/slow glucose is being used up
- Add a 4th enzyme that represents the average other enzyme activity in the extract
    - 'ATP leak'
    - This enzyme functions to turn ATP into ADP and Pi
    - This can function to rate-cap the plummet down of ATP
    - this would be where TX/TL model would be incorporated
- Graph full machinery to system alongside only ATP leak as a comparison
    - atp leak w/o system (baseline) vs
       - 0 can possibly parametrize with available data
    - atp leak w/ system
        - like a battery recharge
- Consider Michaelis-Menten Kinetics for binding reactions
- Figure out why the different enzymatic models look different
    - how are they different and in what cases
    - check the code for the multi-step models to make sure there are no syntax errors
    - perform a parameter search to find where curves look the same and where they look different
        - make them the same and also change to try to understand where the differences come from
   - eventually pick a model
   - try to do an automated parameter sweep - change 1 and keep all the others the same
       - want to consider end points AND dynamics, don't neglect dynamics
- Think about biochemistry point of view
    - how enzyme can be sequestered (with waste and product)
- General tips:
    - graph as many species as possible to better understand 
    - plot different species by scale
    - plot enzymes and their bound state
    
Take-aways from **Richard Meeting (4.27.2020)**
- Consider units, guess from bionumbers
- Consider adding a reaction where nothing goes to glucose
- Write out and understand ODE's for mass-action
- If any negative numbers, simulation is basically invalid
    - maybe step size is too big
- Make a subSBML in bioscrape and add to biocrnpyler with tx/tl
- Can we find data that will validate the model?
    - show that we match data
     - see what models are telling us
     - validate regeneration model
- Steps
1) Validate energy utilization in tX/tL from murray lab
2) Develop/obtain tx/tl model in tubes
3) If it doesn't work - look at other models
4) If it does work - try to connect to other models
    - what features do you want - atp, gtp utilization?
- David Garcia will be a biochemistry cell-free resource


    

**First, let's copy over all the code and triple-triple check for accuracy.** We will add a 4th enzyme that represents ATP leak.

# Simplified model

**Combined**
$$\text{2 ATP + Glucose} \leftrightarrow^{E1} \text{2 ADP + F16P}$$
**Non-ATP Generating**
$$\text{2 ADP + F16P} \leftrightarrow^{E2} \text{2 ATP + Isobutanol}$$
**ATP Generating**
$$\text{3 ADP + Pi + F16P} \leftrightarrow^{E3} \text{3 ATP + Isobutanol}$$
**Spontaneous Hydrolysis / Degradation**
$$\text{ATP} \rightarrow^{E4} \text{ADP + Pi}$$ <br> <br>


Add reverse reactions.

In [2]:
parameters = [('kf', 1), ('kr', 0.1), ('delta', 10)]

x_0 = {
    'glucose': 100,
    'atp':200
}

x_0_atp_leak = {
    'atp': 200
}

In [3]:
species = ['atp', 'glucose', 'adp', 'pi', 'f16p', 'isobutanol']

rxn1_f = (['atp', 'atp', 'glucose'], ['adp', 'adp', 'f16p'], 'massaction', {'k': 'kf'})
rxn1_r = (['adp', 'adp', 'f16p'], ['atp', 'atp', 'glucose'],  'massaction', {'k': 'kr'})

rxn2_f = (['adp', 'adp', 'f16p'], ['atp', 'atp', 'isobutanol'], 'massaction', {'k': 'kf'})
rxn2_r = (['atp', 'atp', 'isobutanol'], ['adp', 'adp', 'f16p'],  'massaction', {'k': 'kr'})

rxn3_f = (['adp', 'adp', 'adp', 'pi', 'f16p'], ['atp', 'atp', 'atp', 'isobutanol'], 'massaction', {'k': 'kf'})
rxn3_r = (['atp', 'atp', 'atp', 'isobutanol'], ['adp', 'adp', 'adp', 'pi', 'f16p'],  'massaction', {'k': 'kr'})

rxn_d_atp = (['atp'], ['adp', 'pi'], 'massaction', {'k': 'delta'})

reactions = [rxn1_f, rxn1_r, rxn2_f, rxn2_r, rxn3_f, rxn3_r, rxn_d_atp]


M = Model(species = species, reactions = reactions, parameters = parameters,
         initial_condition_dict = x_0)
timepoints = np.linspace(0,10,1000)
df_results = py_simulate_model(timepoints, Model = M, stochastic = False)

# Model for only the atp leak
species_atp_leak = ['atp', 'adp', 'pi']
reactions_atp_leak = [rxn_d_atp]
M_atp_leak = Model(species = species_atp_leak, reactions = reactions_atp_leak, parameters = parameters,
                  initial_condition_dict = x_0_atp_leak)
df_results_atp_leak = py_simulate_model(timepoints, Model = M_atp_leak, stochastic = False)

/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:18: UserWarning: The following species are uninitialized and their value has been defaulted to 0: adp, pi, f16p, isobutanol, 
/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:26: UserWarning: The following species are uninitialized and their value has been defaulted to 0: adp, pi, 


In [4]:
# First plot glucose and isobutanol
p = bokeh.plotting.figure(width = 300, height = 250, 
                         x_axis_label = 'time',
                         y_axis_label = 'concentration',
                         title = 'Simplified ATP Rheostat')
p.line(timepoints, df_results['glucose'], color = 'green', legend_label = 'glucose')
p.line(timepoints, df_results['isobutanol'], color = 'orange', legend_label = 'isobutanol')
p.line(timepoints, df_results['f16p'], color = 'purple', legend_label = 'f16p')
p.legend.location = 'center_right'

# Plot ATP and ADP, Pi
p2 = bokeh.plotting.figure(width = 300, height = 250,
                           x_axis_label = 'time',
                         y_axis_label = 'concentration')
p2.line(timepoints, df_results['atp'], color = 'red', legend_label = 'atp')
p2.line(timepoints, df_results['pi'], color = 'blue', legend_label = 'pi')
p2.line(timepoints, df_results['adp'], color = 'green', legend_label = 'adp')
p2.legend.location = 'center_right'

# Plot only ATP leak model
p3 = bokeh.plotting.figure(width = 300, height = 250,
                          x_axis_label = 'time',
                          y_axis_label = 'concentration',
                          title = 'Only ATP Leak')
p3.line(timepoints, df_results_atp_leak['atp'], legend_label = 'atp', color = 'red')


# Show plots
bokeh.io.show(row(p, p2, p3))

## 1 Step Model
### Mass-action propensities and ATP Leak

$$\text{Fuel + Substrate + Enzyme} \leftrightarrow^1 \text{Fuel:Substrate:Enzyme} \rightarrow^2 \text{Waste:Product:Enzyme} \leftrightarrow^3 \text{Waste + Product + Enzyme}$$

**Combined** <br>
$$\text{2 ATP + Glucose + Enzyme1} \leftrightarrow^1 \text{2ATP:Glucose:Enzyme1} \rightarrow^2 \text{2ADP:F16P:Enzyme1} \leftrightarrow^3 \text{2 ADP + F16P + Enzyme1}$$ <br>

**Non-ATP Generating Pathway** <br>
$$\text{F16P + 2 ADP + Enzyme2} \leftrightarrow^4 \text{2ADP:F16P:Enzyme2} \rightarrow^5 \text{2 ATP:Isobutanol:Enzyme2} \leftrightarrow^6 \text{2 ATP + Isobutanol + Enzyme2}$$ <br>

**ATP Generating Pathway** <br>
$$\text{3 ADP + Pi + F16P + Enzyme3} \leftrightarrow^7 \text{3ADPPi:F16P:Enzyme3} \rightarrow^8 \text{3ATP:Isobutanol:Enzyme3} \leftrightarrow^9 \text{3 ATP + Isobutanol + Enzyme3}$$ <br>

**ATP Leak** <br>
$$\text{ATP + Enzyme4} \leftrightarrow^{10} \text{ATP:Enzyme4} \rightarrow^{11} \text{ADPPi:Enzyme4} \leftrightarrow^{12} \text{ADP + Pi + Enzyme4}$$



In [5]:
parameters = [('kf', 10), ('kr', 0.1), ('delta', 10)]

x0 = {
    "glucose":100,
    "atp":200, 
    'e1': 20, 
    'e2':20,
    'e3':20,
    'e4':20
}

x_0_atp_leak = {
    'atp': 200,
    'e4':20
}

In [25]:
species = ['atp', 'glucose', 'e1', '2atp:glucose:e1', '2adp:f16p:e1', 'adp', 'pi', 'f16p',
           'e2', '2adp:f16p:e2','2atp:isobutanol:e2', 
           '3adppi:f16p:e3', 'e3' , '3atp:isobutanol:e3', 'isobutanol',
          'atp:e4', 'adppi:e4', 'e4']

# reaction 1
rxn1_f = (['atp', 'atp', 'glucose', 'e1'], ['2atp:glucose:e1'],
           'massaction',  {'k': 'kf'})
                            
rxn1_r = ( ['2atp:glucose:e1'],['atp', 'atp', 'glucose', 'e1'], 
            'massaction', {'k': 'kr'})

# reaction 2
rxn2_f = ( ['2atp:glucose:e1'],['2adp:f16p:e1'], 
           'massaction', {'k': 'kf'})

# reaction 3
rxn3_f =  ( ['2adp:f16p:e1'], ['adp', 'adp', 'f16p', 'e1'], 
           'massaction', {'k': 'kf'})
 
rxn3_r =  (['adp', 'adp', 'f16p', 'e1'], ['2adp:f16p:e1'],
           'massaction', {'k': 'kr'})

# reaction 4
rxn4_f =  (['f16p', 'adp', 'adp', 'e2'], ['2adp:f16p:e2'],
           'massaction', {'k': 'kf'})

rxn4_r =  ( ['2adp:f16p:e2'], ['f16p', 'adp', 'adp', 'e2'],
           'massaction', {'k': 'kr'})

# reaction 5 
rxn5_f =  (['2adp:f16p:e2'], ['2atp:isobutanol:e2'],
           'massaction', {'k': 'kf'})


# reaction 6
rxn6_f =  (['2atp:isobutanol:e2'], ['atp', 'atp', 'isobutanol', 'e2'],
           'massaction', {'k': 'kf'})

rxn6_r =  (['atp', 'atp', 'isobutanol', 'e2'], ['2atp:isobutanol:e2'],
           'massaction', {'k': 'kr'})
    

# reaction 7
rxn7_f = ( ['adp', 'adp', 'adp', 'pi', 'f16p', 'e3'],['3adppi:f16p:e3'], 
              'massaction', {'k': 'kf'})

rxn7_r = ( ['3adppi:f16p:e3'],['adp', 'adp', 'adp', 'pi', 'f16p', 'e3'], 
              'massaction', {'k': 'kr'})

# reaction 8
rxn8_f = ( ['3adppi:f16p:e3'],['3atp:isobutanol:e3'], 
              'massaction', {'k': 'kf'})

# reaction 9
rxn9_f = ( ['3atp:isobutanol:e3'],['atp', 'atp','atp',  'isobutanol', 'e3'], 
              'massaction', {'k': 'kf'})

rxn9_r = ( ['atp', 'atp', 'atp', 'isobutanol', 'e3'],['3atp:isobutanol:e3'], 
              'massaction', {'k': 'kr'})

# ATP leak
rxn10_f = (["atp", 'e4'], ['atp:e4'], "massaction", {"k":"kf"})
rxn10_r = (['atp:e4'], ["atp", 'e4'],  "massaction", {"k":"kr"})

rxn11_f = (['atp:e4'], ["adppi:e4"],  "massaction", {"k":"kf"})

rxn12_f = ( ["adppi:e4"], ['adp', 'pi', 'e4'], "massaction", {"k":"kf"})
rxn12_r = (['adp', 'pi', 'e4'], ["adppi:e4"] , "massaction", {"k":"kr"})


reactions = [rxn1_f, rxn1_r, rxn2_f, rxn3_f, rxn3_r,rxn4_f,
             rxn4_r, rxn5_f, rxn6_f,  rxn6_r, rxn7_f,
             rxn7_r, rxn8_f, rxn9_f, rxn9_r, 
             rxn10_f, rxn10_r, rxn11_f, rxn12_f, rxn12_r]

# reactions = [rxn1_f, rxn1_r, rxn2_f, rxn3_f, rxn3_r,rxn4_f,
#              rxn4_r, rxn5_f, rxn6_f,  rxn6_r,  
#              rxn10_f, rxn10_r, rxn11_f, rxn12_f, rxn12_r]

M = Model(species = species, reactions = reactions, parameters = parameters, initial_condition_dict = x0)
timepoints = np.linspace(0,10,1000)
df_results = py_simulate_model(timepoints, Model = M, stochastic = False)

# Model for only the atp leak
species_atp_leak = ['atp', 'adp', 'pi', 'e4', 'atp:e4', 'adppi:e4']
reactions_atp_leak = [rxn10_f, rxn10_r, rxn11_f, rxn12_f, rxn12_r]
M_atp_leak = Model(species = species_atp_leak, reactions = reactions_atp_leak, parameters = parameters,
                  initial_condition_dict = x_0_atp_leak)
df_results_atp_leak = py_simulate_model(timepoints, Model = M_atp_leak, stochastic = False)

/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:81: UserWarning: The following species are uninitialized and their value has been defaulted to 0: 2atp:glucose:e1, 2adp:f16p:e1, adp, pi, f16p, 2adp:f16p:e2, 2atp:isobutanol:e2, 3adppi:f16p:e3, 3atp:isobutanol:e3, isobutanol, atp:e4, adppi:e4, 
/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:89: UserWarning: The following species are uninitialized and their value has been defaulted to 0: adp, pi, atp:e4, adppi:e4, 


In [26]:
# First plot glucose and isobutanol
p = bokeh.plotting.figure(width = 300, height = 250, 
                         x_axis_label = 'time',
                         y_axis_label = 'concentration',
                         title = '1 Step Model (massaction)')
p.line(timepoints, df_results['glucose'], color = 'green', legend_label = 'glucose')
p.line(timepoints, df_results['isobutanol'], color = 'orange', legend_label = 'isobutanol')
p.line(timepoints, df_results['f16p'], color = 'purple', legend_label = 'f16p')
p.legend.location = 'center_right'

# Plot ATP and ADP, Pi
p2 = bokeh.plotting.figure(width = 300, height = 250,
                           x_axis_label = 'time',
                         y_axis_label = 'concentration')
p2.line(timepoints, df_results['atp'], color = 'red', legend_label = 'atp')
p2.line(timepoints, df_results['pi'], color = 'blue', legend_label = 'pi')
p2.line(timepoints, df_results['adp'], color = 'green', legend_label = 'adp')
p2.legend.location = 'center_right'

# Plot only ATP leak model
p3 = bokeh.plotting.figure(width = 300, height = 250,
                          x_axis_label = 'time',
                          y_axis_label = 'concentration',
                          title = 'Only ATP Leak')
p3.line(timepoints, df_results_atp_leak['atp'], legend_label = 'atp', color = 'red')


# Show plots
bokeh.io.show(row(p, p2, p3))

## Three step model version 1

$$\text{Substrate + Enzyme} \leftrightarrow^1 \text{Substrate:Enzyme}$$ <br>
$$\text{Fuel + Substrate:Enzyme} \leftrightarrow^2 \text{Fuel:Substrate:Enzyme} \rightarrow^3 \text{Waste:Product:Enzyme} \leftrightarrow^4 \text{Waste + Product:Enzyme}$$ <br>
$$\text{Product:Enzyme} \leftrightarrow^5 \text{Product + Enzyme}$$ <br>

**Common**
$$\text{Glucose + Enzyme1} \leftrightarrow^1 \text{Glucose:Enzyme1}$$ <br>
$$\text{2 ATP + Glucose:Enzyme1} \leftrightarrow^2 \text{2ATP:Glucose:Enzyme1} \rightarrow^3 \text{2adp:f16p:Enzyme1} \leftrightarrow^4 \text{2ADP + F16P:Enzyme1}$$ <br>
$$\text{F16P:Enzyme1} \leftrightarrow^5 \text{F16P + Enzyme1}$$ <br>

**Non-ATP Generating Pathway**
$$\text{F16P + Enzyme2} \leftrightarrow^6 \text{F16P:Enzyme2}$$ <br>
$$\text{2 ADP + F16P:Enzyme2} \leftrightarrow^7 \text{2adp:F16P:Enzyme2} \rightarrow^8 \text{2ATP:Isobutanol:Enzyme2} \leftrightarrow^9 \text{2 ATP + Isobutanol:Enzyme2}$$ <br>
$$\text{Isobutanol:Enzyme2} \leftrightarrow^{10} \text{Isobutanol + Enzyme2}$$ <br>


**ATP Generating Pathway**
$$\text{F16P + Enzyme3} \leftrightarrow^{11} \text{F16P:Enzyme3}$$ <br>
$$\text{3 ADP + Pi + F16P:Enzyme3} \leftrightarrow^{12} \text{3adppi:F16P:Enzyme3} \rightarrow^{13} \text{3ATP:Isobutanol:Enzyme3} \leftrightarrow^{14} \text{3 ATP + Isobutanol:Enzyme3}$$ <br>
$$\text{Isobutanol:Enzyme3} \leftrightarrow^{15} \text{Isobutanol + Enzyme3}$$ <br>


**ATP Leak** <br>
$$\text{ATP + Enzyme4} \leftrightarrow^{16} \text{ATP:Enzyme4} \rightarrow^{17} \text{ADPPi:Enzyme4} \leftrightarrow^{18} \text{ADP + Pi + Enzyme4}$$


In [22]:
parameters = [('kf', 10), ('kr', 0.1), ('delta', 10)]

x_0 = {
    'glucose': 100,
    'atp':200,
    'e1':20,
    'e2':20,
    'e3':20,
    'e4':20
}

x_0_atp_leak = {
    'atp': 200,
    'e4':20
}

In [27]:
species = ['glucose', 'e1', 'atp', 'glucose:e1', '2atp:glucose:e1', '2adp:f16p:e1', 'adp', 'pi', 'f16p:e1', 'f16p',
          'e2', 'f16p:e2', '2adp:f16p:e2', '2atp:isobutanol:e2', 'isobutanol:e2',
          'e3', 'f16p:e3', '3adppi:f16p:e3', '3atp:isobutanol:e3', 'isobutanol:e3', 'isobutanol',
          'e4', 'atp:e4', 'adppi:e4']


rxn1_f = (['glucose', 'e1'], ['glucose:e1'], 'massaction', {'k': 'kf'})
rxn1_r = (['glucose:e1'], ['glucose', 'e1'], 'massaction', {'k': 'kr'})

rxn2_f = (['atp', 'atp', 'glucose:e1'], ['2atp:glucose:e1'], 'massaction', {'k': 'kf'})
rxn2_r = (['2atp:glucose:e1'], ['atp', 'atp', 'glucose:e1'], 'massaction', {'k': 'kr'})

rxn3_f = (['2atp:glucose:e1'], ['2adp:f16p:e1'], 'massaction', {'k': 'kf'})

rxn4_f = (['2adp:f16p:e1'], ['adp', 'adp', 'f16p:e1'], 'massaction', {'k': 'kf'})
rxn4_r = (['adp', 'adp', 'f16p:e1'], ['2adp:f16p:e1'], 'massaction', {'k': 'kr'})

rxn5_f = (['f16p:e1'], ['f16p', 'e1'], 'massaction', {'k': 'kf'})
rxn5_r = (['f16p', 'e1'], ['f16p:e1'], 'massaction', {'k': 'kr'})

rxn6_f = (['f16p', 'e2'], ['f16p:e2'], 'massaction', {'k': 'kf'})
rxn6_r = (['f16p:e2'], ['f16p', 'e2'], 'massaction', {'k': 'kr'})

rxn7_f = (['adp', 'adp','f16p:e2'], ['2adp:f16p:e2'], 'massaction', {'k': 'kf'})
rxn7_r = (['2adp:f16p:e2'], ['adp', 'adp', 'f16p:e2'], 'massaction', {'k': 'kr'})

rxn8_f = (['2adp:f16p:e2'], ['2atp:isobutanol:e2'], 'massaction', {'k': 'kf'})

rxn9_f = (['2atp:isobutanol:e2'], ['atp', 'atp', 'isobutanol:e2'], 'massaction', {'k': 'kf'})
rxn9_r = (['atp', 'atp', 'isobutanol:e2'], ['2atp:isobutanol:e2'], 'massaction', {'k': 'kr'})

rxn10_f = (['isobutanol:e2'], ['isobutanol', 'e2'], 'massaction', {'k': 'kf'})
rxn10_r = (['isobutanol', 'e2'], ['isobutanol:e2'], 'massaction', {'k': 'kr'})

rxn11_f = (['f16p', 'e3'], ['f16p:e3'], 'massaction', {'k': 'kf'})
rxn11_r = ( ['f16p:e3'], ['f16p', 'e3'], 'massaction', {'k': 'kr'})

rxn12_f = (['adp', 'adp', 'adp', 'pi', 'f16p:e3'], ['3adppi:f16p:e3'], 'massaction', {'k': 'kf'})
rxn12_r = (['3adppi:f16p:e3'], ['adp', 'adp', 'adp', 'pi', 'f16p:e3'], 'massaction', {'k': 'kr'})

rxn13_f = (['3adppi:f16p:e3'], ['3atp:isobutanol:e3'], 'massaction', {'k': 'kf'})

rxn14_f = (['3atp:isobutanol:e3'], ['atp', 'atp', 'atp', 'isobutanol:e3'], 'massaction', {'k': 'kf'})
rxn14_r = ( ['atp', 'atp', 'atp', 'isobutanol:e3'], ['3atp:isobutanol:e3'], 'massaction', {'k': 'kr'})

rxn15_f = (['isobutanol:e3'], ['isobutanol', 'e3'], 'massaction', {'k': 'kf'})
rxn15_r = (['isobutanol', 'e3'], ['isobutanol:e3'], 'massaction', {'k': 'kr'})

#ATP Leak
rxn16_f = (["atp", 'e4'], ['atp:e4'], "massaction", {"k":"kf"})
rxn16_r = (['atp:e4'], ["atp", 'e4'],  "massaction", {"k":"kr"})

rxn17_f = (['atp:e4'], ["adppi:e4"],  "massaction", {"k":"kf"})

rxn18_f = ( ["adppi:e4"], ['adp', 'pi', 'e4'], "massaction", {"k":"kf"})
rxn18_r = (['adp', 'pi', 'e4'], ["adppi:e4"] , "massaction", {"k":"kr"})

reactions = [rxn1_f, rxn1_r, rxn2_f, rxn2_r, rxn3_f, rxn4_f, rxn4_r, rxn5_f, rxn5_r, rxn6_f, rxn6_r, rxn7_f, rxn7_r,
            rxn8_f, rxn9_f, rxn9_r, rxn10_f, rxn10_r, rxn11_f, rxn11_r, rxn12_f, rxn12_r, rxn13_f,
            rxn14_f, rxn14_r, rxn15_f, rxn15_r, 
            rxn16_f, rxn16_r, rxn17_f, rxn18_f, rxn18_r]



M = Model(species = species, reactions = reactions, parameters = parameters,
         initial_condition_dict = x_0)
timepoints = np.linspace(0,10,1000)
df_results = py_simulate_model(timepoints, Model = M, stochastic = False)

# Model only for the atp leak
species_atp_leak = ['atp', 'adp', 'pi', 'e4', 'atp:e4', 'adppi:e4']
reactions_atp_leak = [rxn16_f, rxn16_r, rxn17_f, rxn18_f, rxn18_r]
M_atp_leak = Model(species = species_atp_leak, reactions = reactions_atp_leak, parameters = parameters,
         initial_condition_dict = x_0_atp_leak)
df_results_atp_leak = py_simulate_model(timepoints, Model = M_atp_leak, stochastic = False)

/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:66: UserWarning: The following species are uninitialized and their value has been defaulted to 0: glucose:e1, 2atp:glucose:e1, 2adp:f16p:e1, adp, pi, f16p:e1, f16p, f16p:e2, 2adp:f16p:e2, 2atp:isobutanol:e2, isobutanol:e2, f16p:e3, 3adppi:f16p:e3, 3atp:isobutanol:e3, isobutanol:e3, isobutanol, atp:e4, adppi:e4, 
/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:74: UserWarning: The following species are uninitialized and their value has been defaulted to 0: adp, pi, atp:e4, adppi:e4, 


In [28]:
# First plot glucose and isobutanol
p = bokeh.plotting.figure(width = 300, height = 250, 
                         x_axis_label = 'time',
                         y_axis_label = 'concentration',
                         title = '3 Step Model V1 (massaction)')
p.line(timepoints, df_results['glucose'], color = 'green', legend_label = 'glucose')
p.line(timepoints, df_results['isobutanol'], color = 'orange', legend_label = 'isobutanol')
p.line(timepoints, df_results['f16p'], color = 'purple', legend_label = 'f16p')
p.legend.location = 'center_right'

# Plot ATP and ADP, Pi
p2 = bokeh.plotting.figure(width = 300, height = 250,
                           x_axis_label = 'time',
                         y_axis_label = 'concentration')
p2.line(timepoints, df_results['atp'], color = 'red', legend_label = 'atp')
p2.line(timepoints, df_results['pi'], color = 'blue', legend_label = 'pi')
p2.line(timepoints, df_results['adp'], color = 'green', legend_label = 'adp')
p2.legend.location = 'center_right'

# Plot only ATP leak model
p3 = bokeh.plotting.figure(width = 300, height = 250,
                          x_axis_label = 'time',
                          y_axis_label = 'concentration',
                          title = 'Only ATP Leak')
p3.line(timepoints, df_results_atp_leak['atp'], legend_label = 'atp', color = 'red')


# Show plots
bokeh.io.show(row(p, p2, p3))

## Three step model version 2

$$\text{Enzyme + Fuel} \leftrightarrow^1 \text{Enzyme:Fuel}$$ <br>
$$\text{Substrate + Enzyme:Fuel} \leftrightarrow^2 \text{Fuel:Substrate:Enzyme} \rightarrow^3 \text{Waste:Product:Enzyme} \leftrightarrow^4 \text{Waste:Enzyme + Product}$$ <br>
$$\text{Waste:Enzyme}\leftrightarrow^5 \text{Waste + Enzyme}$$ <br>

**Combined**
$$\text{Enzyme1 + 2 ATP} \leftrightarrow^1 \text{Enzyme1:2ATP}$$ <br>
$$\text{Glucose + Enzyme1:2ATP} \leftrightarrow^2 \text{2ATP:Glucose:Enzyme1} \rightarrow^3 \text{2ADP:F16P:Enzyme1} \leftrightarrow^4 \text{2ADP:Enzyme1 + F16P}$$ <br>
$$\text{2ADP:Enzyme1}\leftrightarrow^5 \text{2 ADP + Enzyme1}$$ <br>

**Non-ATP Generating Pathway**
$$\text{Enzyme2 + 2 ADP} \leftrightarrow^6 \text{Enzyme2:2ADP}$$ <br>
$$\text{F16P + Enzyme2:2ADP} \leftrightarrow^7 \text{2ADP:F16P:Enzyme2} \rightarrow^8 \text{2ATP:Isobutanol:Enzyme2} \leftrightarrow^9 \text{2ATP:Enzyme2 + Isobutanol}$$ <br>
$$\text{2ATP:Enzyme2}\leftrightarrow^{10} \text{2 ATP + Enzyme2}$$ <br>

**ATP Generating Pathway**
$$\text{Enzyme3 + 3 ADP + Pi} \leftrightarrow^{11} \text{Enzyme3:3ADPPi}$$ <br>
$$\text{F16P + Enzyme3:3ADPPi} \leftrightarrow^{12} \text{3ADPPi:F16P:Enzyme3} \rightarrow^{13} \text{3ATP:F16P:Enzyme3} \leftrightarrow^{14} \text{3ATP:Enzyme3 + F16P}$$ <br>
$$\text{3ATP:Enzyme3}\leftrightarrow^{15} \text{3 ATP + Enzyme3}$$ <br>

**ATP Leak** <br>
$$\text{ATP + Enzyme4} \leftrightarrow^{16} \text{ATP:Enzyme4} \rightarrow^{17} \text{ADPPi:Enzyme4} \leftrightarrow^{18} \text{ADP + Pi + Enzyme4}$$




In [21]:
parameters = [('kf', 10), ('kr', 0.1), ('delta', 10)]

x_0 = {
    'glucose': 100,
    'atp':200,
    'e1':20,
    'e2':20,
    'e3':20,
    'e4':20
}

x_0_atp_leak = {
    'atp': 200,
    'e4':20
}

In [31]:
species = ['e1', 'atp', 'e1:2atp', '2atp:glucose:e1', '2adp:f16p:e1', '2adp:e1', 'f16p', 'adp', 'pi',
          'e2', 'e2:2adp', '2adp:f16p:e2', '2atp:isobutanol:e2', '2atp:e2', 'isobutanol',
          'e3', 'e2:3adppi', '3adppi:f16p:e3', '3atp:f16p:e3', '3atp:e3',
          'e4', 'atp:e4', 'adppi:e4']


rxn1_f = (['e1', 'atp', 'atp'], ['e1:2atp'], 'massaction', {'k': 'kf'})
rxn1_r = (['e1:2atp'], ['e1', 'atp', 'atp'], 'massaction', {'k': 'kf'})

rxn2_f = (['glucose', 'e1:2atp'], ['2atp:glucose:e1'], 'massaction', {'k': 'kf'})
rxn2_r = (['2atp:glucose:e1'], ['glucose', 'e1:2atp'], 'massaction', {'k': 'kr'})

rxn3_f = (['2atp:glucose:e1'], ['2adp:f16p:e1'], 'massaction', {'k': 'kf'})

rxn4_f = (['2adp:f16p:e1'], ['2adp:e1', 'f16p'], 'massaction', {'k': 'kf'})
rxn4_r = (['2adp:e1', 'f16p'], ['2adp:f16p:e1'], 'massaction', {'k': 'kr'})

rxn5_f = (['2adp:e1'], ['adp', 'adp', 'e1'], 'massaction', {'k': 'kf'})
rxn5_r = (['adp', 'adp', 'e1'], ['2adp:e1'], 'massaction', {'k': 'kr'})

rxn6_f = (['e2', 'adp', 'adp'], ['e2:2adp'], 'massaction', {'k': 'kf'})
rxn6_r = (['e2:2adp'], ['e2', 'adp', 'adp'], 'massaction', {'k': 'kf'})

rxn7_f = (['f16p', 'e2:2adp'], ['2adp:f16p:e2'], 'massaction', {'k': 'kf'})
rxn7_r = (['2adp:f16p:e2'], ['f16p', 'e2:2adp'], 'massaction', {'k': 'kf'})

rxn8_f = (['2adp:f16p:e2'], ['2atp:isobutanol:e2'], 'massaction', {'k': 'kf'})

rxn9_f = (['2atp:isobutanol:e2'], ['2atp:e2', 'isobutanol'], 'massaction', {'k': 'kf'})
rxn9_r = (['2atp:e2', 'isobutanol'], ['2atp:isobutanol:e2'], 'massaction', {'k': 'kr'})

rxn10_f = (['2atp:e2'], ['atp', 'atp', 'e2'], 'massaction', {'k': 'kf'})
rxn10_r = (['atp', 'atp', 'e2'], ['2atp:e2'], 'massaction', {'k': 'kr'})

rxn11_f = (['e3', 'adp', 'adp', 'adp', 'pi'], ['e3:3adppi'], 'massaction', {'k': 'kf'})
rxn11_r = (['e3:3adppi'], ['e3', 'adp', 'adp', 'adp', 'pi'], 'massaction', {'k': 'kr'})

rxn12_f = (['f16p', 'e3:3adppi'], ['3adppi:f16p:e3'], 'massaction', {'k': 'kf'})
rxn12_r = (['3adppi:f16p:e3'], ['f16p', 'e3:3adppi'], 'massaction', {'k': 'kr'})

rxn13_f = (['3adppi:f16p:e3'], ['3atp:f16p:e3'], 'massaction', {'k': 'kf'})

rxn14_f = (['3atp:f16p:e3'], ['3atp:e3', 'f16p'], 'massaction', {'k': 'kf'})
rxn14_r = (['3atp:e3', 'f16p'], ['3atp:f16p:e3'], 'massaction', {'k': 'kr'})

rxn15_f = (['3atp:e3'], ['atp', 'atp', 'atp', 'e3'], 'massaction', {'k': 'kf'})
rxn15_r = (['atp', 'atp', 'atp', 'e3'], ['3atp:e3'], 'massaction', {'k': 'kr'})

#ATP Leak
rxn16_f = (["atp", 'e4'], ['atp:e4'], "massaction", {"k":"kf"})
rxn16_r = (['atp:e4'], ["atp", 'e4'],  "massaction", {"k":"kr"})

rxn17_f = (['atp:e4'], ["adppi:e4"],  "massaction", {"k":"kf"})

rxn18_f = ( ["adppi:e4"], ['adp', 'pi', 'e4'], "massaction", {"k":"kf"})
rxn18_r = (['adp', 'pi', 'e4'], ["adppi:e4"] , "massaction", {"k":"kr"})

reactions = [rxn1_f, rxn1_r, rxn2_f, rxn2_r, rxn3_f, rxn4_f, rxn4_r, rxn5_f, rxn5_r, rxn6_f, rxn6_r, rxn7_f, rxn7_r,
            rxn8_f, rxn9_f, rxn9_r, rxn10_f, rxn10_r, rxn11_f, rxn11_r, rxn12_f, rxn12_r, rxn13_f,
            rxn14_f, rxn14_r, rxn15_f, rxn15_r, 
            rxn16_f, rxn16_r, rxn17_f, rxn18_f, rxn18_r]

M = Model(species = species, reactions = reactions, parameters = parameters,
         initial_condition_dict = x_0)
timepoints = np.linspace(0,100,1000)
df_results = py_simulate_model(timepoints, Model = M, stochastic = False)

# Model only for the atp leak
species_atp_leak = ['atp', 'adp', 'pi', 'e4', 'atp:e4', 'adppi:e4']
reactions_atp_leak = [rxn16_f, rxn16_r, rxn17_f, rxn18_f, rxn18_r]
M_atp_leak = Model(species = species_atp_leak, reactions = reactions_atp_leak, parameters = parameters,
         initial_condition_dict = x_0_atp_leak)
df_results_atp_leak = py_simulate_model(timepoints, Model = M_atp_leak, stochastic = False)

/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:64: UserWarning: The following species are uninitialized and their value has been defaulted to 0: e1:2atp, 2atp:glucose:e1, 2adp:f16p:e1, 2adp:e1, f16p, adp, pi, e2:2adp, 2adp:f16p:e2, 2atp:isobutanol:e2, 2atp:e2, isobutanol, e2:3adppi, 3adppi:f16p:e3, 3atp:f16p:e3, 3atp:e3, atp:e4, adppi:e4, e3:3adppi, 
/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:72: UserWarning: The following species are uninitialized and their value has been defaulted to 0: adp, pi, atp:e4, adppi:e4, 


In [35]:
# First plot glucose and isobutanol
p = bokeh.plotting.figure(width = 300, height = 250, 
                         x_axis_label = 'time',
                         y_axis_label = 'concentration',
                         title = '3 Step Model V2 (massaction)')
p.line(timepoints, df_results['glucose'], color = 'green', legend_label = 'glucose')
p.line(timepoints, df_results['isobutanol'], color = 'orange', legend_label = 'isobutanol')
p.line(timepoints, df_results['f16p'], color = 'purple', legend_label = 'f16p')
p.legend.location = 'center_right'

# Plot ATP and ADP, Pi
p2 = bokeh.plotting.figure(width = 300, height = 250,
                           x_axis_label = 'time',
                         y_axis_label = 'concentration')
p2.line(timepoints, df_results['atp'], color = 'red', legend_label = 'atp')
p2.line(timepoints, df_results['pi'], color = 'blue', legend_label = 'pi')
p2.line(timepoints, df_results['adp'], color = 'green', legend_label = 'adp')
p2.legend.location = 'center_right'

# Plot only ATP leak model
p3 = bokeh.plotting.figure(width = 300, height = 250,
                          x_axis_label = 'time',
                          y_axis_label = 'concentration',
                          title = 'Only ATP Leak')
p3.line(timepoints, df_results_atp_leak['atp'], legend_label = 'atp', color = 'red')



# Show plots
bokeh.io.show(row(p, p2, p3))

## Parameter Reasoning

## Combined Plotting for Parameter Search

In [ ]:
def plot_all(parameters, x_0):
    
    # 1 step model 
    species = ['atp', 'glucose', 'e1', '2atp:glucose:e1', '2adp:f16p:e1', 'adp', 'pi', 'f16p',
           'e2', '2adp:f16p:e2','2atp:isobutanol:e2', 
           '3adppi:f16p:e3', 'e3' , '3atp:isobutanol:e3', 'isobutanol']
    

## Ugly attempt

In [1]:
#Using Bioscrape: Basic Imports

#A Model is a CRN with some bells and whistles
from bioscrape.types import Model

#py_simulate_model is a helper function that takes care of may details for you
from bioscrape.simulator import py_simulate_model

#For arrays and plotting
import numpy as np
import pylab as plt

# Import good plotting packages 
import bokeh.io
import bokeh.plotting
from bokeh.layouts import row
#import bokeh_catplot

import panel as pn

import warnings
warnings.filterwarnings("ignore")

bokeh.io.output_notebook()
pn.extension()

Loading BokehJS ...

In [2]:
k_bf_1_slider = pn.widgets.FloatSlider(name = 'k_bf_1', start = 0, end = 100, step = 0.1, value = 0.378)
k_br_1_slider = pn.widgets.FloatSlider(name = 'k_br_1', start = 0, end = 100, step = 0.1, value = 0.0378)
k_uf_1_slider = pn.widgets.FloatSlider(name = 'k_uf_1', start = 0, end = 100, step = 0.1, value = 0.04)
k_ur_1_slider = pn.widgets.FloatSlider(name = 'k_ur_1', start = 0, end = 100, step = 0.1, value = 0.004)
k_cat_1_slider = pn.widgets.FloatSlider(name = 'k_cat_1', start = 0, end = 1000, step = 1, value = 200)


k_bf_2_slider = pn.widgets.FloatSlider(name = 'k_bf_2', start = 0, end = 100, step = 0.1, value = 0.378)
k_br_2_slider = pn.widgets.FloatSlider(name = 'k_br_2', start = 0, end = 100, step = 0.1, value = 0.0378)
k_uf_2_slider = pn.widgets.FloatSlider(name = 'k_uf_2', start = 0, end = 100, step = 0.1, value = 0.04)
k_ur_2_slider = pn.widgets.FloatSlider(name = 'k_ur_2', start = 0, end = 100, step = 0.1, value = 0.004)
k_cat_2_slider = pn.widgets.FloatSlider(name = 'k_cat_2', start = 0, end = 1000, step = 1, value = 200)


k_bf_3_slider = pn.widgets.FloatSlider(name = 'k_bf_3', start = 0, end = 100, step = 0.1, value = 0.378)
k_br_3_slider = pn.widgets.FloatSlider(name = 'k_br_3', start = 0, end = 100, step = 0.1, value = 0.0378)
k_uf_3_slider = pn.widgets.FloatSlider(name = 'k_uf_3', start = 0, end = 100, step = 0.1, value = 0.04)
k_ur_3_slider = pn.widgets.FloatSlider(name = 'k_ur_3', start = 0, end = 100, step = 0.1, value = 0.004)
k_cat_3_slider = pn.widgets.FloatSlider(name = 'k_cat_3', start = 0, end = 1000, step = 1, value = 200)



In [10]:
@pn.depends(k_bf_1_slider, k_br_1_slider, k_uf_1_slider, k_ur_1_slider, k_cat_1_slider,
           k_bf_2_slider, k_br_2_slider, k_uf_2_slider, k_ur_2_slider, k_cat_2_slider,
           k_bf_3_slider, k_br_3_slider, k_uf_3_slider, k_ur_3_slider, k_cat_3_slider,)

def plot_all(x_0, x_0_atp_leak, k_bf_1 = 0.378, k_br_1 = 0.0378, k_uf_1 = 0.04, k_ur_1 = 0.004, k_cat_1 = 200,
             k_bf_2 = 0.378, k_br_2 = 0.0378, k_uf_2 = 0.04, k_ur_2 = 0.004, k_cat_2 = 200, 
             k_bf_3 = 0.0378, k_br_3 = 0.0378, k_uf_3 = 0.04, k_ur_3 = 0.004, k_cat_3 = 200,
             t_max = 100):

#def plot_all(parameters1, parameters2, parameters3, x_0, x_0_atp_leak, t_max = 100):

    # Define parameter lists here 
    parameters1 = [('k_bf', k_bf_1), ('k_br', k_br_1), ('k_uf', k_uf_1), ('k_ur', k_ur_1), ('k_cat', k_cat_1)]
    parameters2 = [('k_bf', k_bf_2), ('k_br', k_br_2), ('k_uf', k_uf_2), ('k_ur', k_ur_2), ('k_cat', k_cat_2)]
    parameters3 = [('k_bf', k_bf_3), ('k_br', k_br_3), ('k_uf', k_uf_3), ('k_ur', k_ur_3), ('k_cat', k_cat_3)]
    

    timepoints = np.linspace(0,t_max,1000)
    
    # MODEL ONE
    parameters = parameters1
    
    # 1 step model
    species = ['atp', 'glucose', 'e1', '2atp:glucose:e1', '2adp:f16p:e1', 'adp', 'pi', 'f16p',
           'e2', '2adp:f16p:e2','2atp:isobutanol:e2', 
           '3adppi:f16p:e3', 'e3' , '3atp:isobutanol:e3', 'isobutanol',
          'atp:e4', 'adppi:e4', 'e4']

    # reaction 1
    rxn1_f = (['atp', 'atp', 'glucose', 'e1'], ['2atp:glucose:e1'],
               'massaction',  {'k': 'k_bf'})

    rxn1_r = ( ['2atp:glucose:e1'],['atp', 'atp', 'glucose', 'e1'], 
                'massaction', {'k': 'k_br'})

    # reaction 2
    rxn2_f = ( ['2atp:glucose:e1'],['2adp:f16p:e1'], 
               'massaction', {'k': 'k_cat'})

    # reaction 3
    rxn3_f =  ( ['2adp:f16p:e1'], ['adp', 'adp', 'f16p', 'e1'], 
               'massaction', {'k': 'k_uf'})

    rxn3_r =  (['adp', 'adp', 'f16p', 'e1'], ['2adp:f16p:e1'],
               'massaction', {'k': 'k_ur'})

    # reaction 4
    rxn4_f =  (['f16p', 'adp', 'adp', 'e2'], ['2adp:f16p:e2'],
               'massaction', {'k': 'k_bf'})

    rxn4_r =  ( ['2adp:f16p:e2'], ['f16p', 'adp', 'adp', 'e2'],
               'massaction', {'k': 'k_br'})

    # reaction 5 
    rxn5_f =  (['2adp:f16p:e2'], ['2atp:isobutanol:e2'],
               'massaction', {'k': 'k_cat'})


    # reaction 6
    rxn6_f =  (['2atp:isobutanol:e2'], ['atp', 'atp', 'isobutanol', 'e2'],
               'massaction', {'k': 'k_uf'})

    rxn6_r =  (['atp', 'atp', 'isobutanol', 'e2'], ['2atp:isobutanol:e2'],
               'massaction', {'k': 'k_ur'})


    # reaction 7
    rxn7_f = ( ['adp', 'adp', 'adp', 'pi', 'f16p', 'e3'],['3adppi:f16p:e3'], 
                  'massaction', {'k': 'k_bf'})

    rxn7_r = ( ['3adppi:f16p:e3'],['adp', 'adp', 'adp', 'pi', 'f16p', 'e3'], 
                  'massaction', {'k': 'k_br'})

    # reaction 8
    rxn8_f = ( ['3adppi:f16p:e3'],['3atp:isobutanol:e3'], 
                  'massaction', {'k': 'k_cat'})

    # reaction 9
    rxn9_f = ( ['3atp:isobutanol:e3'],['atp', 'atp','atp',  'isobutanol', 'e3'], 
                  'massaction', {'k': 'k_uf'})

    rxn9_r = ( ['atp', 'atp', 'atp', 'isobutanol', 'e3'],['3atp:isobutanol:e3'], 
                  'massaction', {'k': 'k_ur'})

    # ATP leak
    rxn10_f = (["atp", 'e4'], ['atp:e4'], "massaction", {"k":"k_bf"})
    rxn10_r = (['atp:e4'], ["atp", 'e4'],  "massaction", {"k":"k_br"})

    rxn11_f = (['atp:e4'], ["adppi:e4"],  "massaction", {"k":"k_cat"})

    rxn12_f = ( ["adppi:e4"], ['adp', 'pi', 'e4'], "massaction", {"k":"k_uf"})
    rxn12_r = (['adp', 'pi', 'e4'], ["adppi:e4"] , "massaction", {"k":"k_ur"})


    reactions = [rxn1_f, rxn1_r, rxn2_f, rxn3_f, rxn3_r,rxn4_f,
                 rxn4_r, rxn5_f, rxn6_f,  rxn6_r, rxn7_f,
                 rxn7_r, rxn8_f, rxn9_f, rxn9_r, 
                 rxn10_f, rxn10_r, rxn11_f, rxn12_f, rxn12_r]

    # reactions = [rxn1_f, rxn1_r, rxn2_f, rxn3_f, rxn3_r,rxn4_f,
    #              rxn4_r, rxn5_f, rxn6_f,  rxn6_r,  
    #              rxn10_f, rxn10_r, rxn11_f, rxn12_f, rxn12_r]

    M = Model(species = species, reactions = reactions, parameters = parameters, initial_condition_dict = x_0)
    timepoints = np.linspace(0,10,1000)
    model_1_df = py_simulate_model(timepoints, Model = M, stochastic = False)

    # Model for only the atp leak
    species_atp_leak = ['atp', 'adp', 'pi', 'e4', 'atp:e4', 'adppi:e4']
    reactions_atp_leak = [rxn10_f, rxn10_r, rxn11_f, rxn12_f, rxn12_r]
    M_atp_leak = Model(species = species_atp_leak, reactions = reactions_atp_leak, parameters = parameters,
                      initial_condition_dict = x_0_atp_leak)
    model_1_df_atp_leak = py_simulate_model(timepoints, Model = M_atp_leak, stochastic = False)
    
    #return [df_results, df_results_atp_leak]    
    # First plot glucose and isobutanol
    p1 = bokeh.plotting.figure(width = 300, height = 250, 
                             x_axis_label = 'time',
                             y_axis_label = 'concentration',
                             title = '1 Step Model (massaction)')
    p1.line(timepoints, model_1_df['glucose'], color = 'green', legend_label = 'glucose')
    p1.line(timepoints, model_1_df['isobutanol'], color = 'orange', legend_label = 'isobutanol')
    p1.line(timepoints, model_1_df['f16p'], color = 'purple', legend_label = 'f16p')
    p1.legend.location = 'center_right'

    # Plot ATP and ADP, Pi
    p2 = bokeh.plotting.figure(width = 300, height = 250,
                               x_axis_label = 'time',
                             y_axis_label = 'concentration',
                             title =  f" {parameters1}")
    p2.line(timepoints, model_1_df['atp'], color = 'red', legend_label = 'atp')
    p2.line(timepoints, model_1_df['pi'], color = 'blue', legend_label = 'pi')
    p2.line(timepoints, model_1_df['adp'], color = 'green', legend_label = 'adp')
    p2.legend.location = 'center_right'

    # Plot only ATP leak model
    p3 = bokeh.plotting.figure(width = 300, height = 250,
                              x_axis_label = 'time',
                              y_axis_label = 'concentration',
                              title = 'Only ATP Leak')
    p3.line(timepoints, model_1_df_atp_leak['atp'], legend_label = 'atp', color = 'red')

    # MODEL TWO
    parameters = parameters2
    
    # 3 step model v1
    species = ['glucose', 'e1', 'atp', 'glucose:e1', '2atp:glucose:e1', '2adp:f16p:e1', 'adp', 'pi', 'f16p:e1', 'f16p',
              'e2', 'f16p:e2', '2adp:f16p:e2', '2atp:isobutanol:e2', 'isobutanol:e2',
              'e3', 'f16p:e3', '3adppi:f16p:e3', '3atp:isobutanol:e3', 'isobutanol:e3', 'isobutanol',
              'e4', 'atp:e4', 'adppi:e4']


    rxn1_f = (['glucose', 'e1'], ['glucose:e1'], 'massaction', {'k': 'k_bf'})
    rxn1_r = (['glucose:e1'], ['glucose', 'e1'], 'massaction', {'k': 'k_br'})

    rxn2_f = (['atp', 'atp', 'glucose:e1'], ['2atp:glucose:e1'], 'massaction', {'k': 'k_bf'})
    rxn2_r = (['2atp:glucose:e1'], ['atp', 'atp', 'glucose:e1'], 'massaction', {'k': 'k_br'})

    rxn3_f = (['2atp:glucose:e1'], ['2adp:f16p:e1'], 'massaction', {'k': 'k_cat'})

    rxn4_f = (['2adp:f16p:e1'], ['adp', 'adp', 'f16p:e1'], 'massaction', {'k': 'k_uf'})
    rxn4_r = (['adp', 'adp', 'f16p:e1'], ['2adp:f16p:e1'], 'massaction', {'k': 'k_ur'})

    rxn5_f = (['f16p:e1'], ['f16p', 'e1'], 'massaction', {'k': 'k_uf'})
    rxn5_r = (['f16p', 'e1'], ['f16p:e1'], 'massaction', {'k': 'k_ur'})

    rxn6_f = (['f16p', 'e2'], ['f16p:e2'], 'massaction', {'k': 'k_bf'})
    rxn6_r = (['f16p:e2'], ['f16p', 'e2'], 'massaction', {'k': 'k_br'})

    rxn7_f = (['adp', 'adp','f16p:e2'], ['2adp:f16p:e2'], 'massaction', {'k': 'k_bf'})
    rxn7_r = (['2adp:f16p:e2'], ['adp', 'adp', 'f16p:e2'], 'massaction', {'k': 'k_br'})

    rxn8_f = (['2adp:f16p:e2'], ['2atp:isobutanol:e2'], 'massaction', {'k': 'k_cat'})

    rxn9_f = (['2atp:isobutanol:e2'], ['atp', 'atp', 'isobutanol:e2'], 'massaction', {'k': 'k_uf'})
    rxn9_r = (['atp', 'atp', 'isobutanol:e2'], ['2atp:isobutanol:e2'], 'massaction', {'k': 'k_ur'})

    rxn10_f = (['isobutanol:e2'], ['isobutanol', 'e2'], 'massaction', {'k': 'k_uf'})
    rxn10_r = (['isobutanol', 'e2'], ['isobutanol:e2'], 'massaction', {'k': 'k_ur'})

    rxn11_f = (['f16p', 'e3'], ['f16p:e3'], 'massaction', {'k': 'k_bf'})
    rxn11_r = ( ['f16p:e3'], ['f16p', 'e3'], 'massaction', {'k': 'k_br'})

    rxn12_f = (['adp', 'adp', 'adp', 'pi', 'f16p:e3'], ['3adppi:f16p:e3'], 'massaction', {'k': 'k_bf'})
    rxn12_r = (['3adppi:f16p:e3'], ['adp', 'adp', 'adp', 'pi', 'f16p:e3'], 'massaction', {'k': 'k_br'})

    rxn13_f = (['3adppi:f16p:e3'], ['3atp:isobutanol:e3'], 'massaction', {'k': 'k_cat'})

    rxn14_f = (['3atp:isobutanol:e3'], ['atp', 'atp', 'atp', 'isobutanol:e3'], 'massaction', {'k': 'k_uf'})
    rxn14_r = ( ['atp', 'atp', 'atp', 'isobutanol:e3'], ['3atp:isobutanol:e3'], 'massaction', {'k': 'k_ur'})

    rxn15_f = (['isobutanol:e3'], ['isobutanol', 'e3'], 'massaction', {'k': 'k_uf'})
    rxn15_r = (['isobutanol', 'e3'], ['isobutanol:e3'], 'massaction', {'k': 'k_ur'})

    #ATP Leak
    rxn16_f = (["atp", 'e4'], ['atp:e4'], "massaction", {"k":"k_bf"})
    rxn16_r = (['atp:e4'], ["atp", 'e4'],  "massaction", {"k":"k_br"})

    rxn17_f = (['atp:e4'], ["adppi:e4"],  "massaction", {"k":"k_cat"})

    rxn18_f = ( ["adppi:e4"], ['adp', 'pi', 'e4'], "massaction", {"k":"k_uf"})
    rxn18_r = (['adp', 'pi', 'e4'], ["adppi:e4"] , "massaction", {"k":"k_ur"})

    reactions = [rxn1_f, rxn1_r, rxn2_f, rxn2_r, rxn3_f, rxn4_f, rxn4_r, rxn5_f, rxn5_r, rxn6_f, rxn6_r, rxn7_f, rxn7_r,
                rxn8_f, rxn9_f, rxn9_r, rxn10_f, rxn10_r, rxn11_f, rxn11_r, rxn12_f, rxn12_r, rxn13_f,
                rxn14_f, rxn14_r, rxn15_f, rxn15_r, 
                rxn16_f, rxn16_r, rxn17_f, rxn18_f, rxn18_r]

    M = Model(species = species, reactions = reactions, parameters = parameters,
             initial_condition_dict = x_0)
    timepoints = np.linspace(0,10,1000)
    model_2_df = py_simulate_model(timepoints, Model = M, stochastic = False)

    # Model only for the atp leak
    species_atp_leak = ['atp', 'adp', 'pi', 'e4', 'atp:e4', 'adppi:e4']
    reactions_atp_leak = [rxn16_f, rxn16_r, rxn17_f, rxn18_f, rxn18_r]
    M_atp_leak = Model(species = species_atp_leak, reactions = reactions_atp_leak, parameters = parameters,
             initial_condition_dict = x_0_atp_leak)
    model_2_df_atp_leak = py_simulate_model(timepoints, Model = M_atp_leak, stochastic = False)
    
    #return [df_results, df_results_atp_leak]
    
      # First plot glucose and isobutanol
    p4 = bokeh.plotting.figure(width = 300, height = 250, 
                             x_axis_label = 'time',
                             y_axis_label = 'concentration (mM)',
                             title = '3 Step Model V1 (massaction)')
    p4.line(timepoints, model_2_df['glucose'], color = 'green', legend_label = 'glucose')
    p4.line(timepoints, model_2_df['isobutanol'], color = 'orange', legend_label = 'isobutanol')
    p4.line(timepoints, model_2_df['f16p'], color = 'purple', legend_label = 'f16p')
    p4.legend.location = 'center_right'

    # Plot ATP and ADP, Pi
    p5 = bokeh.plotting.figure(width = 300, height = 250,
                               x_axis_label = 'time',
                             y_axis_label = 'concentration ',
                              title =  f" {parameters2}")
    p5.line(timepoints, model_2_df['atp'], color = 'red', legend_label = 'atp')
    p5.line(timepoints, model_2_df['pi'], color = 'blue', legend_label = 'pi')
    p5.line(timepoints, model_2_df['adp'], color = 'green', legend_label = 'adp')
    p5.legend.location = 'center_right'

    # Plot only ATP leak model
    p6 = bokeh.plotting.figure(width = 300, height = 250,
                              x_axis_label = 'time ',
                              y_axis_label = 'concentration',
                              title = 'Only ATP Leak')
    p6.line(timepoints, model_2_df_atp_leak['atp'], legend_label = 'atp', color = 'red')

    parameters = parameters3
    species = ['e1', 'atp', 'e1:2atp', '2atp:glucose:e1', '2adp:f16p:e1', '2adp:e1', 'f16p', '2adp:e1', 'adp', 'pi',
          'e2', 'e2:2adp', '2adp:f16p:e2', '2atp:isobutanol:e2', '2atp:e2', 'isobutanol',
          'e3', 'e2:3adppi', '3adppi:f16p:e3', '3atp:f16p:e3', '3atp:e3']


    rxn1_f = (['e1', 'atp', 'atp'], ['e1:2atp'], 'massaction', {'k': 'k_bf'})
    rxn1_r = (['e1:2atp'], ['e1', 'atp', 'atp'], 'massaction', {'k': 'k_br'})

    rxn2_f = (['glucose', 'e1:2atp'], ['2atp:glucose:e1'], 'massaction', {'k': 'k_bf'})
    rxn2_r = (['2atp:glucose:e1'], ['glucose', 'e1:2atp'], 'massaction', {'k': 'k_br'})

    rxn3_f = (['2atp:glucose:e1'], ['2adp:f16p:e1'], 'massaction', {'k': 'k_cat'})

    rxn4_f = (['2adp:f16p:e1'], ['2adp:e1', 'f16p'], 'massaction', {'k': 'k_uf'})
    rxn4_r = (['2adp:e1', 'f16p'], ['2adp:f16p:e1'], 'massaction', {'k': 'k_ur'})

    rxn5_f = (['2adp:e1'], ['adp', 'adp', 'e1'], 'massaction', {'k': 'k_uf'})
    rxn5_r = (['adp', 'adp', 'e1'], ['2adp:e1'], 'massaction', {'k': 'k_ur'})

    rxn6_f = (['e2', 'adp', 'adp'], ['e2:2adp'], 'massaction', {'k': 'k_bf'})
    rxn6_r = (['e2:2adp'], ['e2', 'adp', 'adp'], 'massaction', {'k': 'k_br'})

    rxn7_f = (['f16p', 'e2:2adp'], ['2adp:f16p:e2'], 'massaction', {'k': 'k_bf'})
    rxn7_r = (['2adp:f16p:e2'], ['f16p', 'e2:2adp'], 'massaction', {'k': 'k_br'})

    rxn8_f = (['2adp:f16p:e2'], ['2atp:isobutanol:e2'], 'massaction', {'k': 'k_cat'})

    rxn9_f = (['2atp:isobutanol:e2'], ['2atp:e2', 'isobutanol'], 'massaction', {'k': 'k_uf'})
    rxn9_r = (['2atp:e2', 'isobutanol'], ['2atp:isobutanol:e2'], 'massaction', {'k': 'k_ur'})

    rxn10_f = (['2atp:e2'], ['atp', 'atp', 'e2'], 'massaction', {'k': 'k_uf'})
    rxn10_r = (['atp', 'atp', 'e2'], ['2atp:e2'], 'massaction', {'k': 'k_ur'})

    rxn11_f = (['e3', 'adp', 'adp', 'adp', 'pi'], ['e3:3adppi'], 'massaction', {'k': 'k_bf'})
    rxn11_r = (['e3:3adppi'], ['e3', 'adp', 'adp', 'adp', 'pi'], 'massaction', {'k': 'k_br'})

    rxn12_f = (['f16p', 'e3:3adppi'], ['3adppi:f16p:e3'], 'massaction', {'k': 'k_bf'})
    rxn12_r = (['3adppi:f16p:e3'], ['f16p', 'e3:3adppi'], 'massaction', {'k': 'k_br'})

    rxn13_f = (['3adppi:f16p:e3'], ['3atp:f16p:e3'], 'massaction', {'k': 'k_cat'})

    rxn14_f = (['3atp:f16p:e3'], ['3atp:e3', 'f16p'], 'massaction', {'k': 'k_uf'})
    rxn14_r = (['3atp:e3', 'f16p'], ['3atp:f16p:e3'], 'massaction', {'k': 'k_ur'})

    rxn15_f = (['3atp:e3'], ['atp', 'atp', 'atp', 'e3'], 'massaction', {'k': 'k_uf'})
    rxn15_r = (['atp', 'atp', 'atp', 'e3'], ['3atp:e3'], 'massaction', {'k': 'k_uf'})


     #ATP Leak
    rxn16_f = (["atp", 'e4'], ['atp:e4'], "massaction", {"k":"k_bf"})
    rxn16_r = (['atp:e4'], ["atp", 'e4'],  "massaction", {"k":"k_br"})

    rxn17_f = (['atp:e4'], ["adppi:e4"],  "massaction", {"k":"k_cat"})

    rxn18_f = ( ["adppi:e4"], ['adp', 'pi', 'e4'], "massaction", {"k":"k_uf"})
    rxn18_r = (['adp', 'pi', 'e4'], ["adppi:e4"] , "massaction", {"k":"k_ur"})

    reactions = [rxn1_f, rxn1_r, rxn2_f, rxn2_r, rxn3_f, rxn4_f, rxn4_r, rxn5_f, rxn5_r, rxn6_f, rxn6_r, rxn7_f, rxn7_r,
                rxn8_f, rxn9_f, rxn9_r, rxn10_f, rxn10_r, rxn11_f, rxn11_r, rxn12_f, rxn12_r, rxn13_f,
                rxn14_f, rxn14_r, rxn15_f, rxn15_r, 
                rxn16_f, rxn16_r, rxn17_f, rxn18_f, rxn18_r]

    M = Model(species = species, reactions = reactions, parameters = parameters,
             initial_condition_dict = x_0)
    timepoints = np.linspace(0,10,1000)
    model_3_df = py_simulate_model(timepoints, Model = M, stochastic = False)

    # Model only for the atp leak
    species_atp_leak = ['atp', 'adp', 'pi', 'e4', 'atp:e4', 'adppi:e4']
    reactions_atp_leak = [rxn16_f, rxn16_r, rxn17_f, rxn18_f, rxn18_r]
    M_atp_leak = Model(species = species_atp_leak, reactions = reactions_atp_leak, parameters = parameters,
             initial_condition_dict = x_0_atp_leak)
    model_3_df_atp_leak = py_simulate_model(timepoints, Model = M_atp_leak, stochastic = False)
    
    #return [df_results, df_results_atp_leak]
    # MODEL THREE
    
    #model_3_df, model_3_df_atp_leak = model3_df(parameters3, x_0, x_0_atp_leak
                                               
      # First plot glucose and isobutanol
    p7 = bokeh.plotting.figure(width = 300, height = 250, 
                             x_axis_label = 'time ',
                             y_axis_label = 'concentration',
                             title = '3 Step Model V2 (massaction)')
    p7.line(timepoints, model_3_df['glucose'], color = 'green', legend_label = 'glucose')
    p7.line(timepoints, model_3_df['isobutanol'], color = 'orange', legend_label = 'isobutanol')
    p7.line(timepoints, model_3_df['f16p'], color = 'purple', legend_label = 'f16p')
    p7.legend.location = 'center_right'

    # Plot ATP and ADP, Pi
    p8 = bokeh.plotting.figure(width = 300, height = 250,
                               x_axis_label = 'time (hrs)',
                             y_axis_label = 'concentration',
                              title =  f" {parameters3}")
    p8.line(timepoints, model_3_df['atp'], color = 'red', legend_label = 'atp')
    p8.line(timepoints, model_3_df['pi'], color = 'blue', legend_label = 'pi')
    p8.line(timepoints, model_3_df['adp'], color = 'green', legend_label = 'adp')
    p8.legend.location = 'center_right'

    # Plot only ATP leak model
    p9 = bokeh.plotting.figure(width = 300, height = 250,
                              x_axis_label = 'time',
                              y_axis_label = 'concentration',
                              title = 'Only ATP Leak')
    p9.line(timepoints, model_3_df_atp_leak['atp'], legend_label = 'atp', color = 'red')
    
    
    #return p1
    bokeh.io.show(row(p1, p2, p3))
    bokeh.io.show(row(p4, p5, p6))
    bokeh.io.show(row(p7, p8, p9))

In [11]:

e = 1.5
atp = 15
x_0 = {
    "glucose":15,
    "atp":atp, 
    'e1': e, 
    'e2':e,
    'e3':e,
    'e4':e
}

x_0_atp_leak = {
    'atp': atp,
    'e4':e
}

In [13]:
widgets = pn.Column(
    pn.Spacer(height=10),
    k_bf_1_slider, k_br_1_slider, k_uf_1_slider, k_ur_1_slider, k_cat_1_slider,
           k_bf_2_slider, k_br_2_slider, k_uf_2_slider, k_ur_2_slider, k_cat_2_slider,
           k_bf_3_slider, k_br_3_slider, k_uf_3_slider, k_ur_3_slider, k_cat_3_slider,
    width=150,
)

left_column = pn.Column(
    pn.Row(pn.Spacer(width=30)), plot_all(x_0, x_0_atp_leak),
)

# Final layout
pn.Column(left_column, pn.Spacer(width=20), widgets)

Column
    [0] Column
        [0] Row
            [0] Spacer(width=30)
        [1] Str(None)
    [1] Spacer(width=20)
    [2] Column(width=150)
        [0] Spacer(height=10)
        [1] FloatSlider(end=100, name='k_bf_1', value=71.4, value_throttled=71.4)
        [2] FloatSlider(end=100, name='k_br_1', value=85.5, value_throttled=85.5)
        [3] FloatSlider(end=100, name='k_uf_1', value=0.04)
        [4] FloatSlider(end=100, name='k_ur_1', value=0.004)
        [5] FloatSlider(end=1000, name='k_cat_1', step=1, value=200)
        [6] FloatSlider(end=100, name='k_bf_2', value=0.378)
        [7] FloatSlider(end=100, name='k_br_2', value=0.0378)
        [8] FloatSlider(end=100, name='k_uf_2', value=0.04)
        [9] FloatSlider(end=100, name='k_ur_2', value=0.004)
        [10] FloatSlider(end=1000, name='k_cat_2', step=1, value=200)
        [11] FloatSlider(end=100, name='k_bf_3', value=0.378)
        [12] FloatSlider(end=100, name='k_br_3', value=0.0378)
        [13] FloatSlider(end=100, name='k_uf_3', value=0.04)
        [14] FloatSlider(end=100, name='k_ur_3', value=0.004)
        [15] FloatSlider(end=1000, name='k_cat_3', step=1, value=200)

# Try minimal model

In [11]:
k_bf_1_slider = pn.widgets.FloatSlider(name = 'k_bf_1', start = 0, end = 100, step = 0.1, value = 0.378)
k_br_1_slider = pn.widgets.FloatSlider(name = 'k_br_1', start = 0, end = 100, step = 0.1, value = 0.0378)
k_uf_1_slider = pn.widgets.FloatSlider(name = 'k_uf_1', start = 0, end = 100, step = 0.1, value = 0.04)
k_ur_1_slider = pn.widgets.FloatSlider(name = 'k_ur_1', start = 0, end = 100, step = 0.1, value = 0.004)
k_cat_1_slider = pn.widgets.FloatSlider(name = 'k_cat_1', start = 0, end = 1000, step = 1, value = 200)

In [27]:
def model1_df(parameters, x_0, x_0_atp_leak):
    
    # 1 step model
    species = ['atp', 'glucose', 'e1', '2atp:glucose:e1', '2adp:f16p:e1', 'adp', 'pi', 'f16p',
           'e2', '2adp:f16p:e2','2atp:isobutanol:e2', 
           '3adppi:f16p:e3', 'e3' , '3atp:isobutanol:e3', 'isobutanol',
          'atp:e4', 'adppi:e4', 'e4']

    # reaction 1
    rxn1_f = (['atp', 'atp', 'glucose', 'e1'], ['2atp:glucose:e1'],
               'massaction',  {'k': 'k_bf'})

    rxn1_r = ( ['2atp:glucose:e1'],['atp', 'atp', 'glucose', 'e1'], 
                'massaction', {'k': 'k_br'})

    # reaction 2
    rxn2_f = ( ['2atp:glucose:e1'],['2adp:f16p:e1'], 
               'massaction', {'k': 'k_cat'})

    # reaction 3
    rxn3_f =  ( ['2adp:f16p:e1'], ['adp', 'adp', 'f16p', 'e1'], 
               'massaction', {'k': 'k_uf'})

    rxn3_r =  (['adp', 'adp', 'f16p', 'e1'], ['2adp:f16p:e1'],
               'massaction', {'k': 'k_ur'})

    # reaction 4
    rxn4_f =  (['f16p', 'adp', 'adp', 'e2'], ['2adp:f16p:e2'],
               'massaction', {'k': 'k_bf'})

    rxn4_r =  ( ['2adp:f16p:e2'], ['f16p', 'adp', 'adp', 'e2'],
               'massaction', {'k': 'k_br'})

    # reaction 5 
    rxn5_f =  (['2adp:f16p:e2'], ['2atp:isobutanol:e2'],
               'massaction', {'k': 'k_cat'})


    # reaction 6
    rxn6_f =  (['2atp:isobutanol:e2'], ['atp', 'atp', 'isobutanol', 'e2'],
               'massaction', {'k': 'k_uf'})

    rxn6_r =  (['atp', 'atp', 'isobutanol', 'e2'], ['2atp:isobutanol:e2'],
               'massaction', {'k': 'k_ur'})


    # reaction 7
    rxn7_f = ( ['adp', 'adp', 'adp', 'pi', 'f16p', 'e3'],['3adppi:f16p:e3'], 
                  'massaction', {'k': 'k_bf'})

    rxn7_r = ( ['3adppi:f16p:e3'],['adp', 'adp', 'adp', 'pi', 'f16p', 'e3'], 
                  'massaction', {'k': 'k_br'})

    # reaction 8
    rxn8_f = ( ['3adppi:f16p:e3'],['3atp:isobutanol:e3'], 
                  'massaction', {'k': 'k_cat'})

    # reaction 9
    rxn9_f = ( ['3atp:isobutanol:e3'],['atp', 'atp','atp',  'isobutanol', 'e3'], 
                  'massaction', {'k': 'k_uf'})

    rxn9_r = ( ['atp', 'atp', 'atp', 'isobutanol', 'e3'],['3atp:isobutanol:e3'], 
                  'massaction', {'k': 'k_ur'})

    # ATP leak
    rxn10_f = (["atp", 'e4'], ['atp:e4'], "massaction", {"k":"k_bf"})
    rxn10_r = (['atp:e4'], ["atp", 'e4'],  "massaction", {"k":"k_br"})

    rxn11_f = (['atp:e4'], ["adppi:e4"],  "massaction", {"k":"k_cat"})

    rxn12_f = ( ["adppi:e4"], ['adp', 'pi', 'e4'], "massaction", {"k":"k_uf"})
    rxn12_r = (['adp', 'pi', 'e4'], ["adppi:e4"] , "massaction", {"k":"k_ur"})


    reactions = [rxn1_f, rxn1_r, rxn2_f, rxn3_f, rxn3_r,rxn4_f,
                 rxn4_r, rxn5_f, rxn6_f,  rxn6_r, rxn7_f,
                 rxn7_r, rxn8_f, rxn9_f, rxn9_r, 
                 rxn10_f, rxn10_r, rxn11_f, rxn12_f, rxn12_r]

    # reactions = [rxn1_f, rxn1_r, rxn2_f, rxn3_f, rxn3_r,rxn4_f,
    #              rxn4_r, rxn5_f, rxn6_f,  rxn6_r,  
    #              rxn10_f, rxn10_r, rxn11_f, rxn12_f, rxn12_r]

    M = Model(species = species, reactions = reactions, parameters = parameters, initial_condition_dict = x_0)
    timepoints = np.linspace(0,10,1000)
    df_results = py_simulate_model(timepoints, Model = M, stochastic = False)

    # Model for only the atp leak
    species_atp_leak = ['atp', 'adp', 'pi', 'e4', 'atp:e4', 'adppi:e4']
    reactions_atp_leak = [rxn10_f, rxn10_r, rxn11_f, rxn12_f, rxn12_r]
    M_atp_leak = Model(species = species_atp_leak, reactions = reactions_atp_leak, parameters = parameters,
                      initial_condition_dict = x_0_atp_leak)
    df_results_atp_leak = py_simulate_model(timepoints, Model = M_atp_leak, stochastic = False)
    
    return [df_results, df_results_atp_leak]

In [28]:
@pn.depends(k_bf_1_slider.param.value, k_br_1_slider.param.value,
            k_uf_1_slider.param.value, k_ur_1_slider.param.value, k_cat_1_slider.param.value,)

   
def plot_all(k_bf_1 = 0.378, k_br_1 = 0.0378, k_uf_1 = 0.04, k_ur_1 = 0.004, k_cat_1 = 200,
             t_max = 100):
  
 # def plot_all(parameters1, parameters2, parameters3, x_0, x_0_atp_leak, t_max = 100):
    x_0 = {
        "glucose":15,
        "atp":atp, 
        'e1': e, 
        'e2':e,
        'e3':e,
        'e4':e
    }

    x_0_atp_leak = { 
        'atp': atp,
        'e4':e
    }
    
    # Define parameter lists here 
    parameters = [('k_bf', k_bf_1), ('k_br', k_br_1), ('k_uf', k_uf_1), ('k_ur', k_ur_1), ('k_cat', k_cat_1)]
    parameters1 = parameters

    timepoints = np.linspace(0,t_max,1000)
    
    # MODEL ONE
    
#     # 1 step model
#     species = ['atp', 'glucose', 'e1', '2atp:glucose:e1', '2adp:f16p:e1', 'adp', 'pi', 'f16p',
#            'e2', '2adp:f16p:e2','2atp:isobutanol:e2', 
#            '3adppi:f16p:e3', 'e3' , '3atp:isobutanol:e3', 'isobutanol',
#           'atp:e4', 'adppi:e4', 'e4']

#     # reaction 1
#     rxn1_f = (['atp', 'atp', 'glucose', 'e1'], ['2atp:glucose:e1'],
#                'massaction',  {'k': 'k_bf'})

#     rxn1_r = ( ['2atp:glucose:e1'],['atp', 'atp', 'glucose', 'e1'], 
#                 'massaction', {'k': 'k_br'})

#     # reaction 2
#     rxn2_f = ( ['2atp:glucose:e1'],['2adp:f16p:e1'], 
#                'massaction', {'k': 'k_cat'})

#     # reaction 3
#     rxn3_f =  ( ['2adp:f16p:e1'], ['adp', 'adp', 'f16p', 'e1'], 
#                'massaction', {'k': 'k_uf'})

#     rxn3_r =  (['adp', 'adp', 'f16p', 'e1'], ['2adp:f16p:e1'],
#                'massaction', {'k': 'k_ur'})

#     # reaction 4
#     rxn4_f =  (['f16p', 'adp', 'adp', 'e2'], ['2adp:f16p:e2'],
#                'massaction', {'k': 'k_bf'})

#     rxn4_r =  ( ['2adp:f16p:e2'], ['f16p', 'adp', 'adp', 'e2'],
#                'massaction', {'k': 'k_br'})

#     # reaction 5 
#     rxn5_f =  (['2adp:f16p:e2'], ['2atp:isobutanol:e2'],
#                'massaction', {'k': 'k_cat'})


#     # reaction 6
#     rxn6_f =  (['2atp:isobutanol:e2'], ['atp', 'atp', 'isobutanol', 'e2'],
#                'massaction', {'k': 'k_uf'})

#     rxn6_r =  (['atp', 'atp', 'isobutanol', 'e2'], ['2atp:isobutanol:e2'],
#                'massaction', {'k': 'k_ur'})


#     # reaction 7
#     rxn7_f = ( ['adp', 'adp', 'adp', 'pi', 'f16p', 'e3'],['3adppi:f16p:e3'], 
#                   'massaction', {'k': 'k_bf'})

#     rxn7_r = ( ['3adppi:f16p:e3'],['adp', 'adp', 'adp', 'pi', 'f16p', 'e3'], 
#                   'massaction', {'k': 'k_br'})

#     # reaction 8
#     rxn8_f = ( ['3adppi:f16p:e3'],['3atp:isobutanol:e3'], 
#                   'massaction', {'k': 'k_cat'})

#     # reaction 9
#     rxn9_f = ( ['3atp:isobutanol:e3'],['atp', 'atp','atp',  'isobutanol', 'e3'], 
#                   'massaction', {'k': 'k_uf'})

#     rxn9_r = ( ['atp', 'atp', 'atp', 'isobutanol', 'e3'],['3atp:isobutanol:e3'], 
#                   'massaction', {'k': 'k_ur'})

#     # ATP leak
#     rxn10_f = (["atp", 'e4'], ['atp:e4'], "massaction", {"k":"k_bf"})
#     rxn10_r = (['atp:e4'], ["atp", 'e4'],  "massaction", {"k":"k_br"})

#     rxn11_f = (['atp:e4'], ["adppi:e4"],  "massaction", {"k":"k_cat"})

#     rxn12_f = ( ["adppi:e4"], ['adp', 'pi', 'e4'], "massaction", {"k":"k_uf"})
#     rxn12_r = (['adp', 'pi', 'e4'], ["adppi:e4"] , "massaction", {"k":"k_ur"})


#     reactions = [rxn1_f, rxn1_r, rxn2_f, rxn3_f, rxn3_r,rxn4_f,
#                  rxn4_r, rxn5_f, rxn6_f,  rxn6_r, rxn7_f,
#                  rxn7_r, rxn8_f, rxn9_f, rxn9_r, 
#                  rxn10_f, rxn10_r, rxn11_f, rxn12_f, rxn12_r]

#     # reactions = [rxn1_f, rxn1_r, rxn2_f, rxn3_f, rxn3_r,rxn4_f,
#     #              rxn4_r, rxn5_f, rxn6_f,  rxn6_r,  
#     #              rxn10_f, rxn10_r, rxn11_f, rxn12_f, rxn12_r]

#     M = Model(species = species, reactions = reactions, parameters = parameters, initial_condition_dict = x_0)
#     timepoints = np.linspace(0,10,1000)
#     model_1_df = py_simulate_model(timepoints, Model = M, stochastic = False)

#     # Model for only the atp leak
#     species_atp_leak = ['atp', 'adp', 'pi', 'e4', 'atp:e4', 'adppi:e4']
#     reactions_atp_leak = [rxn10_f, rxn10_r, rxn11_f, rxn12_f, rxn12_r]
#     M_atp_leak = Model(species = species_atp_leak, reactions = reactions_atp_leak, parameters = parameters,
#                       initial_condition_dict = x_0_atp_leak)
#     model_1_df_atp_leak = py_simulate_model(timepoints, Model = M_atp_leak, stochastic = False)
    
    #return [df_results, df_results_atp_leak]    
    # First plot glucose and isobutanol
    
    model_1_df, model_1_df_atp_leak = model1_df(parameters1, x_0, x_0_atp_leak)


    p1 = bokeh.plotting.figure(width = 300, height = 250, 
                             x_axis_label = 'time',
                             y_axis_label = 'concentration',
                             title = '1 Step Model (massaction)')
    p1.line(timepoints, model_1_df['glucose'], color = 'green', legend_label = 'glucose')
    p1.line(timepoints, model_1_df['isobutanol'], color = 'orange', legend_label = 'isobutanol')
    p1.line(timepoints, model_1_df['f16p'], color = 'purple', legend_label = 'f16p')
    p1.legend.location = 'center_right'

    # Plot ATP and ADP, Pi
    p2 = bokeh.plotting.figure(width = 300, height = 250,
                               x_axis_label = 'time',
                             y_axis_label = 'concentration',
                             title =  f" {parameters1}")
    p2.line(timepoints, model_1_df['atp'], color = 'red', legend_label = 'atp')
    p2.line(timepoints, model_1_df['pi'], color = 'blue', legend_label = 'pi')
    p2.line(timepoints, model_1_df['adp'], color = 'green', legend_label = 'adp')
    p2.legend.location = 'center_right'

    # Plot only ATP leak model
    p3 = bokeh.plotting.figure(width = 300, height = 250,
                              x_axis_label = 'time',
                              y_axis_label = 'concentration',
                              title = 'Only ATP Leak')
    p3.line(timepoints, model_1_df_atp_leak['atp'], legend_label = 'atp', color = 'red')

    
    #return p1
    return row(p1, p2, p3)
    #bokeh.io.show(row(p1, p2, p3))


In [29]:
widgets = pn.Column(
    pn.Spacer(height=10),
    k_bf_1_slider, k_br_1_slider, k_uf_1_slider, k_ur_1_slider, k_cat_1_slider,
    width=150,
)

left_column = pn.Column(
    pn.Row(pn.Spacer(width=30)), plot_all
)

# Final layout
pn.Column(left_column, pn.Spacer(width=20), widgets)

/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:84: UserWarning: The following species are uninitialized and their value has been defaulted to 0: 2atp:glucose:e1, 2adp:f16p:e1, adp, pi, f16p, 2adp:f16p:e2, 2atp:isobutanol:e2, 3adppi:f16p:e3, 3atp:isobutanol:e3, isobutanol, atp:e4, adppi:e4, 
/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:92: UserWarning: The following species are uninitialized and their value has been defaulted to 0: adp, pi, atp:e4, adppi:e4, 


Column
    [0] Column
        [0] Row
            [0] Spacer(width=30)
        [1] ParamFunction(function)
    [1] Spacer(width=20)
    [2] Column(width=150)
        [0] Spacer(height=10)
        [1] FloatSlider(end=100, name='k_bf_1', value=11.100000000000001, value_throttled=11.100000000000001)
        [2] FloatSlider(end=100, name='k_br_1', value=32.300000000000004, value_throttled=32.300000000000004)
        [3] FloatSlider(end=100, name='k_uf_1', value=11.9, value_throttled=11.9)
        [4] FloatSlider(end=100, name='k_ur_1', value=15.8, value_throttled=15.8)
        [5] FloatSlider(end=1000, name='k_cat_1', step=1, value=307, value_throttled=307)

In [7]:

e = 1.5
atp = 15
x_0 = {
    "glucose":15,
    "atp":atp, 
    'e1': e, 
    'e2':e,
    'e3':e,
    'e4':e
}

x_0_atp_leak = { 
    'atp': atp,
    'e4':e
}